In [48]:
import numpy as np
import pandas as pd
import sklearn
import nltk
import re
import json
import torch
import pickle
import tensorflow as tf

import keras
from keras.preprocessing import image
from sklearn.model_selection import train_test_split

from tqdm import tqdm

In [2]:
movies = pd.read_csv('archive/movies_metadata.csv')
print("Shape: ", movies.shape)
print("Features: ", movies.columns)

Shape:  (45466, 24)
Features:  Index(['adult', 'belongs_to_collection', 'budget', 'genres', 'homepage', 'id',
       'imdb_id', 'original_language', 'original_title', 'overview',
       'popularity', 'poster_path', 'production_companies',
       'production_countries', 'release_date', 'revenue', 'runtime',
       'spoken_languages', 'status', 'tagline', 'title', 'video',
       'vote_average', 'vote_count'],
      dtype='object')


/Users/anshverma/opt/anaconda3/envs/python37/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3166: DtypeWarning: Columns (10) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [3]:
movies['original_title']

0                          Toy Story
1                            Jumanji
2                   Grumpier Old Men
3                  Waiting to Exhale
4        Father of the Bride Part II
                    ...             
45461                        رگ خواب
45462            Siglo ng Pagluluwal
45463                       Betrayal
45464            Satana likuyushchiy
45465                       Queerama
Name: original_title, Length: 45466, dtype: object

In [4]:
print("Shape: ", movies.shape)
print("Features: ", movies.columns)

Shape:  (45466, 24)
Features:  Index(['adult', 'belongs_to_collection', 'budget', 'genres', 'homepage', 'id',
       'imdb_id', 'original_language', 'original_title', 'overview',
       'popularity', 'poster_path', 'production_companies',
       'production_countries', 'release_date', 'revenue', 'runtime',
       'spoken_languages', 'status', 'tagline', 'title', 'video',
       'vote_average', 'vote_count'],
      dtype='object')


In [5]:
movies['overview'][1]

"When siblings Judy and Peter discover an enchanted board game that opens the door to a magical world, they unwittingly invite Alan -- an adult who's been trapped inside the game for 26 years -- into their living room. Alan's only hope for freedom is to finish the game, which proves risky as all three find themselves running from giant rhinoceroses, evil monkeys and other terrifying creatures."

In [6]:
movies.head()['imdb_id']

0    tt0114709
1    tt0113497
2    tt0113228
3    tt0114885
4    tt0113041
Name: imdb_id, dtype: object

In [7]:
movies.head()['genres']

0    [{'id': 16, 'name': 'Animation'}, {'id': 35, '...
1    [{'id': 12, 'name': 'Adventure'}, {'id': 14, '...
2    [{'id': 10749, 'name': 'Romance'}, {'id': 35, ...
3    [{'id': 35, 'name': 'Comedy'}, {'id': 18, 'nam...
4                       [{'id': 35, 'name': 'Comedy'}]
Name: genres, dtype: object

In [8]:
movies.head()['poster_path']

0    /rhIRbceoE9lR4veEXuwCC2wARtG.jpg
1    /vzmL6fP7aPKNKPRTFnZmiUfciyV.jpg
2    /6ksm1sjKMFLbO7UY2i6G1ju9SML.jpg
3    /16XOMpEaLWkrcPqSQqhTmeJuqQl.jpg
4    /e64sOI48hQXyru7naBFyssKFxVd.jpg
Name: poster_path, dtype: object

In [9]:
movies.head()['genres'][0]

"[{'id': 16, 'name': 'Animation'}, {'id': 35, 'name': 'Comedy'}, {'id': 10751, 'name': 'Family'}]"

In [10]:
movies.head()['genres'][1]

"[{'id': 12, 'name': 'Adventure'}, {'id': 14, 'name': 'Fantasy'}, {'id': 10751, 'name': 'Family'}]"

In [11]:
movies.columns.values

array(['adult', 'belongs_to_collection', 'budget', 'genres', 'homepage',
       'id', 'imdb_id', 'original_language', 'original_title', 'overview',
       'popularity', 'poster_path', 'production_companies',
       'production_countries', 'release_date', 'revenue', 'runtime',
       'spoken_languages', 'status', 'tagline', 'title', 'video',
       'vote_average', 'vote_count'], dtype=object)

In [12]:
movies['popularity']

0        21.946943
1        17.015539
2          11.7129
3         3.859495
4         8.387519
           ...    
45461     0.072051
45462     0.178241
45463     0.903007
45464     0.003503
45465     0.163015
Name: popularity, Length: 45466, dtype: object

In [13]:
movies.dropna(subset = ['poster_path', 'genres'], inplace=True)

In [14]:
movies.dropna(subset = ["overview"], inplace=True)
print(movies.shape)
print(movies)

movies.fillna(0, inplace=True)

movies = movies[0: 986]

(44166, 24)
       adult                              belongs_to_collection    budget  \
0      False  {'id': 10194, 'name': 'Toy Story Collection', ...  30000000   
1      False                                                NaN  65000000   
2      False  {'id': 119050, 'name': 'Grumpy Old Men Collect...         0   
3      False                                                NaN  16000000   
4      False  {'id': 96871, 'name': 'Father of the Bride Col...         0   
...      ...                                                ...       ...   
45461  False                                                NaN         0   
45462  False                                                NaN         0   
45463  False                                                NaN         0   
45464  False                                                NaN         0   
45465  False                                                NaN         0   

                                                  genres  \
0  

In [15]:
movies

adult                              belongs_to_collection    budget  \
0     False  {'id': 10194, 'name': 'Toy Story Collection', ...  30000000   
1     False                                                  0  65000000   
2     False  {'id': 119050, 'name': 'Grumpy Old Men Collect...         0   
3     False                                                  0  16000000   
4     False  {'id': 96871, 'name': 'Father of the Bride Col...         0   
...     ...                                                ...       ...   
996   False                                                  0   3000000   
997   False                                                  0         0   
998   False                                                  0  48000000   
999   False                                                  0   6000000   
1000  False                                                  0    812000   

                                                 genres  \
0     [{'id': 16, 'name': 'Animation'}, {'id': 35, '...   
1     [{'id': 12, 'name': 'Adventure'}, {'id': 14, '...   
2     [{'id': 10749, 'name': 'Romance'}, {'id': 35, ...   
3     [{'id': 35, 'name': 'Comedy'}, {'id': 18, 'nam...   
4                        [{'id': 35, 'name': 'Comedy'}]   
...                                                 ...   
996   [{'id': 16, 'name': 'Animation'}, {'id': 10751...   
997   [{'id': 16, 'name': 'Animation'}, {'id': 18, '...   
998                   [{'id': 12, 'name': 'Adventure'}]   
999   [{'id': 35, 'name': 'Comedy'}, {'id': 10751, '...   
1000  [{'id': 16, 'name': 'Animation'}, {'id': 10751...   

                                  homepage     id    imdb_id  \
0     http://toystory.disney.com/toy-story    862  tt0114709   
1                                        0   8844  tt0113497   
2                                        0  15602  tt0113228   
3                                        0  31357  tt0114885   
4                                        0  11862  tt0113041   
...                                    ...    ...        ...   
996                                      0   9078  tt0057546   
997                                      0  29682  tt0041890   
998                                      0   8367  tt0102798   
999                                      0    433  tt0058331   
1000                                     0  11360  tt0033563   

     original_language                 original_title  \
0                   en                      Toy Story   
1                   en                        Jumanji   
2                   en               Grumpier Old Men   
3                   en              Waiting to Exhale   
4                   en    Father of the Bride Part II   
...                ...                            ...   
996                 en         The Sword in the Stone   
997                 en            So Dear to My Heart   
998                 en  Robin Hood: Prince of Thieves   
999                 en                   Mary Poppins   
1000                en                          Dumbo   

                                               overview  ... release_date  \
0     Led by Woody, Andy's toys live happily in his ...  ...   1995-10-30   
1     When siblings Judy and Peter discover an encha...  ...   1995-12-15   
2     A family wedding reignites the ancient feud be...  ...   1995-12-22   
3     Cheated on, mistreated and stepped on, the wom...  ...   1995-12-22   
4     Just when George Banks has recovered from his ...  ...   1995-02-10   
...                                                 ...  ...          ...   
996   Wart is a young boy who aspires to be a knight...  ...   1963-12-25   
997   The tale of Jeremiah Kincaid and his quest to ...  ...   1948-11-29   
998   When the dastardly Sheriff of Nottingham murde...  ...   1991-06-14   
999   The movie combines a diverting story, songs, c...  ...   1964-08-27   
1000  Dumbo is a baby elephant born with oversized e...  ...   1941-10-22   

     

In [16]:
movies['poster_path'].isnull().sum()

0

In [17]:
# @Source: https://johannesbader.ch/blog/tutorial-download-posters-with-the-movie-database-api-in-python/"
import os
import re
import requests

CONFIG_PATTERN = 'http://api.themoviedb.org/3/configuration?api_key={key}'
IMG_PATTERN = 'http://api.themoviedb.org/3/movie/{imdbid}/images?api_key={key}' 
KEY = '6f2ceb0e0b459afe90f6e854fcd410eb'
            
def _get_json(url):
    r = requests.get(url)
    return r.json()
    
def _download_images(titles, urls, path):
    """download all images in list 'urls' to 'path' """
    filePathList = []
    print(len(urls), len(titles))
    zipped = list(zip(titles, urls))
    i = 0
    for title, url in zipped: 
        r = requests.get(url)
        filetype = r.headers['content-type'].split('/')[-1]
        filename = re.sub(r'\W+', ' ', title).lower().strip().replace(" ", "-") + '.jpg'
        print(i)
        filepath = os.path.join(path, filename)
        filePathList.append(filepath)
        #commented this out so that won't redownload data every single time
        if r.status_code == 200:
            with open(filepath,'wb') as w:
                w.write(r.content)
        i+=1
    
    return path, filePathList 

def get_poster_url(imdbid):
    """ 
    given IMDB id, returns the corresponding url for
    poster jpg
    
    Args: 
        imdbid (str): IMDB id
    Return: 
        url (str): image url of poster image from 'themoviedb.org'
                of the maximum available size. 
    """
    config = _get_json(CONFIG_PATTERN.format(key=KEY))
    base_url = config['images']['base_url']
    sizes = config['images']['poster_sizes']   # sorted in ascending order
    
    def size_str_to_int(x):
        return float("inf") if x == 'original' else int(x[1:])
    
    # retrieve image of max size
    max_size = max(sizes, key=size_str_to_int)
    
    try: 
        posters = _get_json(IMG_PATTERN.format(key=KEY,imdbid=imdbid))['posters']
    except: 
        print(imdbid)
    
    if len(posters) == 0:
        return None
    
    rel_path = posters[0]['file_path']
    url = "{0}{1}{2}".format(base_url, max_size, rel_path)
    
    return url

In [18]:
# RUN THIS FUNCTION TO DOWNLOAD JPG IMAGES
def tmdb_posters():
    """ download posters with imdb_id from dataset """
    
    if not os.path.exists('images_movies_genre'):
        os.makedirs('images_movies_genre')
    filePathList = []
    titles = []
    urls = []
    checkIter = []
    n = 0
    for index, row in movies.iterrows():
        title = str(row['title'])
        url = get_poster_url(row['imdb_id'])
        
        # skip iteration if poster cannot be located
        if not url:
            checkIter.append(0)
            continue
            
        checkIter.append(1)
        titles.append(title)
        urls.append(url)
        n += 1
        #print(n)
        if n == 1000:
            break
            
        # SET LIMIT FOR NUMBER OF IMAGES TO DOWNLOAD

    path, filePathList = _download_images(titles, urls, 'images_movies_genre')
    retList = []
    counter = 0
    for i in checkIter: 
        if i == 0: 
            retList.append('NaN')
        elif i == 1: 
            retList.append(filePathList[counter])
            counter+=1
    return path, retList

path, filePathList = tmdb_posters()

955 955
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
27

In [19]:
filename = "/Users/anshverma/Documents/GitHub/MovieGenrePrediction/ImageData"
filenameTwo = "/Users/anshverma/Documents/GitHub/MovieGenrePrediction/Genres"
fileNameThree =  "/Users/anshverma/Documents/GitHub/MovieGenrePrediction/xTrain"
fileNameFour =  "/Users/anshverma/Documents/GitHub/MovieGenrePrediction/xTest"
fileNameFive =  "/Users/anshverma/Documents/GitHub/MovieGenrePrediction/yTrain"
fileNameSix =  "/Users/anshverma/Documents/GitHub/MovieGenrePrediction/yTest"

def loadTrain(): 
    filehandler = open(fileNameThree, 'rb') 
    xTrain = np.load(filehandler, allow_pickle=True) #pickle.load(filehandler)
    filehandlerTwo = open(fileNameFive, 'rb')
    yTrain = np.load(filehandlerTwo, allow_pickle=True)
    return xTrain, yTrain

def loadTest(): 
    filehandler = open(fileNameFour, 'rb') 
    xTest = np.load(filehandler, allow_pickle=True) #pickle.load(filehandler)
    filehandlerTwo = open(fileNameSix, 'rb') 
    yTest = np.load(filehandlerTwo, allow_pickle=True) #pickle.load(filehandler)
    return xTest, yTest

def saveImages(imageList, genres, pathOne, pathTwo): 
    filehandler = open(pathOne, 'wb')
    np.save(filehandler, imageList)
    filehandlerTwo = open(pathTwo, 'wb')
    np.save(filehandlerTwo, genres)
    #pickle.dump(imageList, filehandler)
        
def loadImages(): 
    filehandler = open(filename, 'rb') 
    files = np.load(filehandler, allow_pickle=True) #pickle.load(filehandler)
    return files

def loadGenres(): 
    filehandlerTwo = open(filenameTwo, 'rb')
    genres = np.load(filehandlerTwo, allow_pickle=True)
    return genres

def load(filePath): 
    loader = csv

def tempSave(genres): 
    genres.to_csv(path_or_buf = filenameTwo)
    
def saveTesting(csv, path): 
    csv.to_csv(path_or_buf = path)
    
def fromCsv(path): 
    return pd.read_csv(path)

In [20]:
# Converting images to array
X = []

for path in tqdm(filePathList):
    try: 
        img = image.load_img(path, target_size=(224, 224, 3))
        img = image.img_to_array(img)
        img = img/255.0
        X.append(img)
    except: 
        X.append('NaN')
        continue
    
X = np.array(X)

100%|██████████| 986/986 [00:28<00:00, 34.29it/s]
/Users/anshverma/opt/anaconda3/envs/python37/lib/python3.7/site-packages/ipykernel_launcher.py:14: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray
  


In [39]:
X = X[0:986]

In [22]:
movies.insert(len(movies.columns), "imageArrays", X, True)

In [132]:
print(type(X))
print(type(X[0]))
print(type(X[0][0]))
print(type(X[0][0][0]))
print(type(X[0][0][0][0]))

<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
<class 'numpy.float32'>


In [145]:
dataType = type(errorVectors[0][0])

In [ ]:
"""
errorVectors = []
for i in range(len(X)): 
    for j in range(len(X[i])): 
        k = 0
        while (k < len(X[i][j])):       
            l = 0
            lenLists = len(X[i][j][k])
            while (l < lenLists): 
                if type(X[i][j][k][l]) != dataType:
                    if ((k + 1) < lenLists): 
                        X[i][j][k] = X[i][j][k + 1]
                        k -= 1
                    else: 
                        np.delete(X, k, 0)
                    errorVectors.append(X[i][j][k])
                    .X[i][j][k]
                l += 1
            k += 1
                #X[i][j][k][l] = float(X[i][j][k][l])
"""
errorVectors = []
for i in range(len(X)): 
    for j in range(len(X[i])): 
        for j in range(len(X[i][j])): 
            for k in range(len(X[i][j])): 
                lenLists = len(X[i][j][k])
                for l in range(lenLists): 
                    if type(X[i][j][k][l]) != dataType:
                        np.delete(X[i][j], k, None)
                        errorVectors.append(X[i][j][k])
errorVectors

In [150]:
for error in errorVectors: 
    for e in error: 
        if (dataType != (type(e))): 
            print(e)
            print(error)
            print(type(e))

N
N
<class 'str'>
a
a
<class 'str'>
N
N
<class 'str'>
N
N
<class 'str'>
a
a
<class 'str'>
N
N
<class 'str'>
N
N
<class 'str'>
a
a
<class 'str'>
N
N
<class 'str'>
N
N
<class 'str'>
a
a
<class 'str'>
N
N
<class 'str'>
N
N
<class 'str'>
a
a
<class 'str'>
N
N
<class 'str'>
N
N
<class 'str'>
a
a
<class 'str'>
N
N
<class 'str'>
N
N
<class 'str'>
a
a
<class 'str'>
N
N
<class 'str'>
N
N
<class 'str'>
a
a
<class 'str'>
N
N
<class 'str'>
N
N
<class 'str'>
a
a
<class 'str'>
N
N
<class 'str'>
N
N
<class 'str'>
a
a
<class 'str'>
N
N
<class 'str'>
N
N
<class 'str'>
a
a
<class 'str'>
N
N
<class 'str'>
N
N
<class 'str'>
a
a
<class 'str'>
N
N
<class 'str'>
N
N
<class 'str'>
a
a
<class 'str'>
N
N
<class 'str'>
N
N
<class 'str'>
a
a
<class 'str'>
N
N
<class 'str'>
N
N
<class 'str'>
a
a
<class 'str'>
N
N
<class 'str'>
N
N
<class 'str'>
a
a
<class 'str'>
N
N
<class 'str'>
N
N
<class 'str'>
a
a
<class 'str'>
N
N
<class 'str'>


KeyboardInterrupt: 

In [134]:
torch.Tensor(X)

TypeError: can't convert np.ndarray of type numpy.object_. The only supported types are: float64, float32, float16, int64, int32, int16, int8, uint8, and bool.

In [23]:
#Padding
#reference: https://ai-pool.com/d/padding-images-with-numpy
def pad(img, h, w):
    top_pad = np.floor((h - img.shape[0]) / 2).astype(np.uint16)
    bottom_pad = np.ceil((h - img.shape[0]) / 2).astype(np.uint16)
    right_pad = np.ceil((w - img.shape[1]) / 2).astype(np.uint16)
    left_pad = np.floor((w - img.shape[1]) / 2).astype(np.uint16)
    return np.copy(np.pad(img, ((top_pad, bottom_pad), (left_pad, right_pad), (0, 0)), mode='constant', constant_values=0))

In [24]:
#checking if padding works
img = image.load_img('images_movies_genre/toy-story.jpg', target_size=(224, 224, 3))
new_img_array=pad(X[0], 512, 512)
new_img=image.array_to_img(new_img_array)
new_img.show()

In [25]:
import ast
#reference-https://www.geeksforgeeks.org/adding-new-column-to-existing-dataframe-in-pandas/
def genre_list(str):
    arr=ast.literal_eval(str)
    genreList=[dict['name'] for dict in arr]
    return genreList

In [26]:
genre_list_collection=[]
for i in movies['genres']:
    genre_list_collection+=[genre_list(i)]
genre_list_collection[0]

['Animation', 'Comedy', 'Family']

In [27]:
#adding a column called genre_list which contains all the genres of the movies in a list
movies.insert(5, "genre_list", genre_list_collection, True)
print("Features: ", movies.columns)
movies['genre_list']

Features:  Index(['adult', 'belongs_to_collection', 'budget', 'genres', 'homepage',
       'genre_list', 'id', 'imdb_id', 'original_language', 'original_title',
       'overview', 'popularity', 'poster_path', 'production_companies',
       'production_countries', 'release_date', 'revenue', 'runtime',
       'spoken_languages', 'status', 'tagline', 'title', 'video',
       'vote_average', 'vote_count', 'imageArrays'],
      dtype='object')


0        [Animation, Comedy, Family]
1       [Adventure, Fantasy, Family]
2                  [Romance, Comedy]
3           [Comedy, Drama, Romance]
4                           [Comedy]
                    ...             
996              [Animation, Family]
997       [Animation, Drama, Family]
998                      [Adventure]
999        [Comedy, Family, Fantasy]
1000             [Animation, Family]
Name: genre_list, Length: 986, dtype: object

In [28]:
all_genres = sum(genre_list_collection,[])
len(set(all_genres))

20

In [29]:
#One hot encoding the genres
from sklearn.preprocessing import MultiLabelBinarizer
mlb = MultiLabelBinarizer()
mlb.fit(movies['genre_list'].values)
genreLabelsList=mlb.transform(movies['genre_list'])
print(genreLabelsList.shape)
#TODO Add the one hot encoded genres to the movies dataframe
genre_labels=pd.DataFrame(genreLabelsList, columns=mlb.classes_)
print(genre_labels)

(986, 20)
     Action  Adventure  Animation  Comedy  Crime  Documentary  Drama  Family  \
0         0          0          1       1      0            0      0       1   
1         0          1          0       0      0            0      0       1   
2         0          0          0       1      0            0      0       0   
3         0          0          0       1      0            0      1       0   
4         0          0          0       1      0            0      0       0   
..      ...        ...        ...     ...    ...          ...    ...     ...   
981       0          0          1       0      0            0      0       1   
982       0          0          1       0      0            0      1       1   
983       0          1          0       0      0            0      0       0   
984       0          0          0       1      0            0      0       1   
985       0          0          1       0      0            0      0       1   

     Fantasy  Foreign  Histor

In [30]:
genre_labels.to_csv('GenreLabels.csv', index=False)

In [31]:
mlb.classes_

array(['Action', 'Adventure', 'Animation', 'Comedy', 'Crime',
       'Documentary', 'Drama', 'Family', 'Fantasy', 'Foreign', 'History',
       'Horror', 'Music', 'Mystery', 'Romance', 'Science Fiction',
       'TV Movie', 'Thriller', 'War', 'Western'], dtype=object)

In [32]:
overviews=pd.DataFrame(movies["overview"])
movies_with_overviews=pd.concat([overviews, genre_labels], axis=1)
movies_with_overviews.head()
#movies_with_overveiws=genre_labels
#movies_with_overviews["overview"]=movies["overview"]

overview  Action  Adventure  \
0  Led by Woody, Andy's toys live happily in his ...     0.0        0.0   
1  When siblings Judy and Peter discover an encha...     0.0        1.0   
2  A family wedding reignites the ancient feud be...     0.0        0.0   
3  Cheated on, mistreated and stepped on, the wom...     0.0        0.0   
4  Just when George Banks has recovered from his ...     0.0        0.0   

   Animation  Comedy  Crime  Documentary  Drama  Family  Fantasy  ...  \
0        1.0     1.0    0.0          0.0    0.0     1.0      0.0  ...   
1        0.0     0.0    0.0          0.0    0.0     1.0      1.0  ...   
2        0.0     1.0    0.0          0.0    0.0     0.0      0.0  ...   
3        0.0     1.0    0.0          0.0    1.0     0.0      0.0  ...   
4        0.0     1.0    0.0          0.0    0.0     0.0      0.0  ...   

   History  Horror  Music  Mystery  Romance  Science Fiction  TV Movie  \
0      0.0     0.0    0.0      0.0      0.0              0.0       0.0   
1      0.0     0.0    0.0      0.0      0.0              0.0       0.0   
2      0.0     0.0    0.0      0.0      1.0              0.0       0.0   
3      0.0     0.0    0.0      0.0      1.0              0.0       0.0   
4      0.0     0.0    0.0      0.0      0.0              0.0       0.0   

   Thriller  War  Western  
0       0.0  0.0      0.0  
1       0.0  0.0      0.0  
2       0.0  0.0      0.0  
3       0.0  0.0      0.0  
4       0.0  0.0      0.0  

[5 rows x 21 columns]

In [33]:
overviews=pd.DataFrame(movies["overview"])
movies_with_overviews=pd.concat([overviews, genre_labels], axis=1)
movies_with_overviews.head()
movies_with_overviews.dropna(subset = ["Action"], inplace=True)
#movies.dropna(subset = ["overview"], inplace=True)

In [34]:
movies_with_overviews

overview  Action  Adventure  \
0    Led by Woody, Andy's toys live happily in his ...     0.0        0.0   
1    When siblings Judy and Peter discover an encha...     0.0        1.0   
2    A family wedding reignites the ancient feud be...     0.0        0.0   
3    Cheated on, mistreated and stepped on, the wom...     0.0        0.0   
4    Just when George Banks has recovered from his ...     0.0        0.0   
..                                                 ...     ...        ...   
981  Herbie is a car - but no ordinary car. The sto...     0.0        0.0   
982  The living Volkswagen Beetle helps a old lady ...     0.0        0.0   
983  Young Travis Coates is left to take care of th...     0.0        1.0   
984  Hayley Mills plays twins who, unknown to their...     0.0        0.0   
985  A young girl comes to an embittered town and c...     0.0        0.0   

     Animation  Comedy  Crime  Documentary  Drama  Family  Fantasy  ...  \
0          1.0     1.0    0.0          0.0    0.0     1.0      0.0  ...   
1          0.0     0.0    0.0          0.0    0.0     1.0      1.0  ...   
2          0.0     1.0    0.0          0.0    0.0     0.0      0.0  ...   
3          0.0     1.0    0.0          0.0    1.0     0.0      0.0  ...   
4          0.0     1.0    0.0          0.0    0.0     0.0      0.0  ...   
..         ...     ...    ...          ...    ...     ...      ...  ...   
981        1.0     0.0    0.0          0.0    0.0     1.0      0.0  ...   
982        1.0     0.0    0.0          0.0    1.0     1.0      0.0  ...   
983        0.0     0.0    0.0          0.0    0.0     0.0      0.0  ...   
984        0.0     1.0    0.0          0.0    0.0     1.0      1.0  ...   
985        1.0     0.0    0.0          0.0    0.0     1.0      0.0  ...   

     History  Horror  Music  Mystery  Romance  Science Fiction  TV Movie  \
0        0.0     0.0    0.0      0.0      0.0              0.0       0.0   
1        0.0     0.0    0.0      0.0      0.0              0.0       0.0   
2        0.0     0.0    0.0      0.0      1.0              0.0       0.0   
3        0.0     0.0    0.0      0.0      1.0              0.0       0.0   
4        0.0     0.0    0.0      0.0      0.0              0.0       0.0   
..       ...     ...    ...      ...      ...              ...       ...   
981      0.0     0.0    0.0      0.0      0.0              0.0       0.0   
982      0.0     0.0    0.0      0.0      0.0              0.0       0.0   
983      0.0     0.0    0.0      0.0      0.0              0.0       0.0   
984      0.0     0.0    0.0      0.0      0.0              0.0       0.0   
985      0.0     0.0    0.0      0.0      0.0              0.0       0.0   

     Thriller  War  Western  
0         0.0  0.0      0.0  
1         0.0  0.0      0.0  
2         0.0  0.0      0.0  
3         0.0  0.0      0.0  
4         0.0  0.0      0.0  
..        ...  ...      ...  
981       0.0  0.0      0.0  
982       0.0  0.0      0.0  
983       0.0  0.0      0.0  
984       0.0  0.0      0.0  
985       0.0  0.0      0.0  

[986 rows x 21 columns]

In [35]:
filename = "/Users/anshverma/Documents/GitHub/MovieGenrePrediction/ImageData"
import numpy as np
def loadImages(): 
    filehandler = open(filename, 'rb') 
    files = np.load(filehandler, allow_pickle=True) #pickle.load(filehandler)
    return files

In [36]:
newX = loadImages()

In [37]:
print("Shape: ", movies_with_overviews.shape)
print("Features: ", movies_with_overviews.columns)
movies_with_overviews.to_csv('MoviesWithOverviews.csv', index=False)

Shape:  (986, 21)
Features:  Index(['overview', 'Action', 'Adventure', 'Animation', 'Comedy', 'Crime',
       'Documentary', 'Drama', 'Family', 'Fantasy', 'Foreign', 'History',
       'Horror', 'Music', 'Mystery', 'Romance', 'Science Fiction', 'TV Movie',
       'Thriller', 'War', 'Western'],
      dtype='object')


In [38]:
movies.shape

(986, 26)

In [39]:
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/anshverma/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [40]:
# Text cleaning
#reference: https://www.analyticsvidhya.com/blog/2019/04/predicting-movie-genres-nlp-multi-label-classification/
from nltk.corpus import stopwords
stop_words = set(stopwords.words('english'))

def clean_text(text): 
    #removing everything except letters and converting to lower case
    text = re.sub("[^a-zA-Z]"," ",str(text))
    text = ' '.join(text.split())
    text = text.lower() 
    return text

# Removing stopwords such as the, and, to, or etc
def remove_stopwords(text):
    no_stopword_text = [w for w in text.split() if not w in stop_words]
    return ' '.join(no_stopword_text)

In [41]:
plot_summaries=[]
for text in movies['overview']:
    cleanText=clean_text(text)
    textWithoutStopwords=remove_stopwords(cleanText)
    plot_summaries+=[textWithoutStopwords]
movies.insert(11, "plot_summary", plot_summaries, True)
print("Features: ", movies.columns)

Features:  Index(['adult', 'belongs_to_collection', 'budget', 'genres', 'homepage',
       'genre_list', 'id', 'imdb_id', 'original_language', 'original_title',
       'overview', 'plot_summary', 'popularity', 'poster_path',
       'production_companies', 'production_countries', 'release_date',
       'revenue', 'runtime', 'spoken_languages', 'status', 'tagline', 'title',
       'video', 'vote_average', 'vote_count', 'imageArrays'],
      dtype='object')


In [42]:
movies["plot_summary"]

0       led woody andy toys live happily room andy bir...
1       siblings judy peter discover enchanted board g...
2       family wedding reignites ancient feud next doo...
3       cheated mistreated stepped women holding breat...
4       george banks recovered daughter wedding receiv...
                              ...                        
996     wart young boy aspires knight squire hunting t...
997     tale jeremiah kincaid quest raise champion lam...
998     dastardly sheriff nottingham murders robin fat...
999     movie combines diverting story songs color seq...
1000    dumbo baby elephant born oversized ears suprem...
Name: plot_summary, Length: 986, dtype: object

In [69]:
"""convert to numpy after"""
#movies_NP = movies.to_numpy()
#genre_labels_NP = genre_labels.to_numpy()
#random_state = 42 makes the division random, don't know what (= 42) is; can be other
#numbers
X_train, X_test, y_train, y_test = train_test_split(movies, genre_labels, test_size=0.20, random_state=42)

In [70]:
X_train

adult belongs_to_collection    budget  \
772  False                     0         0   
336  False                     0         0   
905  False                     0         0   
531  False                     0         0   
470  False                     0  13000000   
..     ...                   ...       ...   
107  False                     0         0   
271  False                     0  15000000   
875  False                     0   2500000   
437  False                     0  57000000   
103  False                     0  24000000   

                                                genres  \
772                                                 []   
336  [{'id': 35, 'name': 'Comedy'}, {'id': 10749, '...   
905  [{'id': 18, 'name': 'Drama'}, {'id': 10749, 'n...   
531  [{'id': 18, 'name': 'Drama'}, {'id': 10751, 'n...   
470                      [{'id': 18, 'name': 'Drama'}]   
..                                                 ...   
107                      [{'id': 80, 'name': 'Crime'}]   
271  [{'id': 35, 'name': 'Comedy'}, {'id': 18, 'nam...   
875  [{'id': 35, 'name': 'Comedy'}, {'id': 18, 'nam...   
437  [{'id': 80, 'name': 'Crime'}, {'id': 28, 'name...   
103  [{'id': 18, 'name': 'Drama'}, {'id': 10749, 'n...   

                                     homepage  \
772                                         0   
336                                         0   
905                                         0   
531                                         0   
470                                         0   
..                                        ...   
107                                         0   
271                                         0   
875                                         0   
437  http://www.warnerbros.com/demolition-man   
103                                         0   

                           genre_list      id    imdb_id original_language  \
772                                []  124306  tt0106810                en   
336                 [Comedy, Romance]   60855  tt0109655                en   
905                  [Drama, Romance]    8356  tt0050105                en   
531                   [Drama, Family]   43535  tt0111194                en   
470                           [Drama]    7984  tt0107207                en   
..                                ...     ...        ...               ...   
107                           [Crime]   96357  tt0113276                en   
271          [Comedy, Drama, Romance]   24070  tt0110538                en   
875          [Comedy, Drama, Romance]     164  tt0054698                en   
437  [Crime, Action, Science Fiction]    9739  tt0106697                en   
103                  [Drama, Romance]     688  tt0112579                en   

                    original_title  ...      revenue runtime  \
772  En compagnie d'Antonin Artaud  ...          0.0    90.0   
336               Double Happiness  ...     759393.0    87.0   
905          An Affair to Remember  ...          0.0   111.0   
531         A Simple Twist of Fate  ...          0.0   106.0   
470      In the Name of the Father  ...   65796862.0   133.0   
..                             ...  ...          ...     ...   
107   Headless Body in Topless Bar  ...          0.0   110.0   
271                     Mixed Nuts  ...          0.0    97.0   
875         Breakfast at Tiffany's  ...    9500000.0   110.0   
437                 Demolition Man  ...  159055768.0   115.0   
103  The Bridges of Madison County  ...  182016617.0   135.0   

                                      spoken_languages    status  \
772                                                 []  Released   
336  [{'iso_639_1': 'cn', 'name': '广州话 / 廣州話'}, {'i...  Released   
905  [{'iso_639_1': 'en', 'name': 'English'}, {'iso...  Released   
531           [{'iso_639_1': 'en', 'name': 'English'}]  Released   
470           [{'iso_639_1': 'en', 'name': 'English'}]  Released   
..                                                 .

In [71]:
for val in X_train: 
    print(val)

adult
belongs_to_collection
budget
genres
homepage
genre_list
id
imdb_id
original_language
original_title
overview
plot_summary
popularity
poster_path
production_companies
production_countries
release_date
revenue
runtime
spoken_languages
status
tagline
title
video
vote_average
vote_count
imageArrays


In [72]:
#saveImages(newX, movies['genre_list']) 
saveImages(X_train, X_test, fileNameThree, fileNameFour)
saveImages(y_train, y_test, fileNameFive, fileNameSix)

In [73]:
tempSave(genre_labels)

In [74]:
images = loadImages()

In [75]:
genres = loadGenres()

OSError: Failed to interpret file <_io.BufferedReader name='/Users/anshverma/Documents/GitHub/MovieGenrePrediction/Genres'> as a pickle

In [96]:
[i for i in range(9)]

[0, 1, 2, 3, 4, 5, 6, 7, 8]

In [101]:
a = np.array([i for i in range(0, 9)])
b = np.array([a for i in range(9)])
c = np.array([b for i in range(9)])

In [104]:
print(type(a))
print(type(b))
print(type(c))

<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
<class 'numpy.ndarray'>


In [103]:
torch.Tensor(c)

tensor([[[0., 1., 2., 3., 4., 5., 6., 7., 8.],
         [0., 1., 2., 3., 4., 5., 6., 7., 8.],
         [0., 1., 2., 3., 4., 5., 6., 7., 8.],
         [0., 1., 2., 3., 4., 5., 6., 7., 8.],
         [0., 1., 2., 3., 4., 5., 6., 7., 8.],
         [0., 1., 2., 3., 4., 5., 6., 7., 8.],
         [0., 1., 2., 3., 4., 5., 6., 7., 8.],
         [0., 1., 2., 3., 4., 5., 6., 7., 8.],
         [0., 1., 2., 3., 4., 5., 6., 7., 8.]],

        [[0., 1., 2., 3., 4., 5., 6., 7., 8.],
         [0., 1., 2., 3., 4., 5., 6., 7., 8.],
         [0., 1., 2., 3., 4., 5., 6., 7., 8.],
         [0., 1., 2., 3., 4., 5., 6., 7., 8.],
         [0., 1., 2., 3., 4., 5., 6., 7., 8.],
         [0., 1., 2., 3., 4., 5., 6., 7., 8.],
         [0., 1., 2., 3., 4., 5., 6., 7., 8.],
         [0., 1., 2., 3., 4., 5., 6., 7., 8.],
         [0., 1., 2., 3., 4., 5., 6., 7., 8.]],

        [[0., 1., 2., 3., 4., 5., 6., 7., 8.],
         [0., 1., 2., 3., 4., 5., 6., 7., 8.],
         [0., 1., 2., 3., 4., 5., 6., 7., 8.],
         

In [115]:
type(XImages_train)

numpy.ndarray

In [116]:
XImages_train = X_train['imageArrays']
XImages_train = XImages_train.to_numpy()
type(XImages_train[0])

numpy.ndarray

In [117]:
type(XImages_train[0][0])

numpy.ndarray

In [118]:
type(XImages_train[0][0][0])

numpy.ndarray

In [119]:
type(XImages_train[0][0][0][0])

numpy.float32

In [120]:
"""Assuming the data is already completely preproccessed, and has the right dimensions"""

'Assuming the data is already completely preproccessed, and has the right dimensions'

In [123]:
XImages_train p

array([array([[[0.5254902 , 0.42745098, 0.5803922 ],
        [0.58431375, 0.4862745 , 0.6392157 ],
        [0.39215687, 0.29411766, 0.44705883],
        ...,
        [0.41960785, 0.28235295, 0.4392157 ],
        [0.56078434, 0.41568628, 0.5764706 ],
        [0.4627451 , 0.31764707, 0.47843137]],

       [[0.56078434, 0.4627451 , 0.6156863 ],
        [0.44313726, 0.34509805, 0.49803922],
        [0.5137255 , 0.41568628, 0.5686275 ],
        ...,
        [0.4       , 0.26666668, 0.4117647 ],
        [0.56078434, 0.41960785, 0.5686275 ],
        [0.54509807, 0.40392157, 0.5529412 ]],

       [[0.47843137, 0.38039216, 0.53333336],
        [0.5921569 , 0.49411765, 0.64705884],
        [0.5686275 , 0.47058824, 0.62352943],
        ...,
        [0.53333336, 0.39607844, 0.5529412 ],
        [0.37254903, 0.22745098, 0.3882353 ],
        [0.45490196, 0.30980393, 0.47058824]],

       ...,

       [[0.00784314, 0.02352941, 0.01960784],
        [0.        , 0.        , 0.        ],
        [0.0941

In [131]:
type(newX[0][0][0][0])

numpy.float32

In [121]:
from torch.utils.data import TensorDataset
from torch.utils.data import DataLoader
XImages_train = X_train['imageArrays'].values
#XImages_train = XImages_train.to_numpy()
#XImages_train.astype(np.float32)
yImages_train = y_train.to_numpy()
tensor_y = torch.Tensor(yImages_train) # transform to torch tensor
tensor_x = torch.Tensor(XImages_train) 
trainDataset = TensorDataset(tensor_y,tensor_x) # create your datset

[array([[[0.5254902 , 0.42745098, 0.5803922 ],
        [0.58431375, 0.4862745 , 0.6392157 ],
        [0.39215687, 0.29411766, 0.44705883],
        ...,
        [0.41960785, 0.28235295, 0.4392157 ],
        [0.56078434, 0.41568628, 0.5764706 ],
        [0.4627451 , 0.31764707, 0.47843137]],

       [[0.56078434, 0.4627451 , 0.6156863 ],
        [0.44313726, 0.34509805, 0.49803922],
        [0.5137255 , 0.41568628, 0.5686275 ],
        ...,
        [0.4       , 0.26666668, 0.4117647 ],
        [0.56078434, 0.41960785, 0.5686275 ],
        [0.54509807, 0.40392157, 0.5529412 ]],

       [[0.47843137, 0.38039216, 0.53333336],
        [0.5921569 , 0.49411765, 0.64705884],
        [0.5686275 , 0.47058824, 0.62352943],
        ...,
        [0.53333336, 0.39607844, 0.5529412 ],
        [0.37254903, 0.22745098, 0.3882353 ],
        [0.45490196, 0.30980393, 0.47058824]],

       ...,

       [[0.00784314, 0.02352941, 0.01960784],
        [0.        , 0.        , 0.        ],
        [0.09411765, 

TypeError: can't convert np.ndarray of type numpy.object_. The only supported types are: float64, float32, float16, int64, int32, int16, int8, uint8, and bool.

In [79]:
type(XImages_train)

pandas.core.series.Series

In [80]:
XImages_train.to_numpy()

array([array([[[0.5254902 , 0.42745098, 0.5803922 ],
        [0.58431375, 0.4862745 , 0.6392157 ],
        [0.39215687, 0.29411766, 0.44705883],
        ...,
        [0.41960785, 0.28235295, 0.4392157 ],
        [0.56078434, 0.41568628, 0.5764706 ],
        [0.4627451 , 0.31764707, 0.47843137]],

       [[0.56078434, 0.4627451 , 0.6156863 ],
        [0.44313726, 0.34509805, 0.49803922],
        [0.5137255 , 0.41568628, 0.5686275 ],
        ...,
        [0.4       , 0.26666668, 0.4117647 ],
        [0.56078434, 0.41960785, 0.5686275 ],
        [0.54509807, 0.40392157, 0.5529412 ]],

       [[0.47843137, 0.38039216, 0.53333336],
        [0.5921569 , 0.49411765, 0.64705884],
        [0.5686275 , 0.47058824, 0.62352943],
        ...,
        [0.53333336, 0.39607844, 0.5529412 ],
        [0.37254903, 0.22745098, 0.3882353 ],
        [0.45490196, 0.30980393, 0.47058824]],

       ...,

       [[0.00784314, 0.02352941, 0.01960784],
        [0.        , 0.        , 0.        ],
        [0.0941

In [77]:
from torch.utils.data import TensorDataset
from torch.utils.data import DataLoader

tensor_y = torch.Tensor(y_test) # transform to torch tensor
tensor_x = torch.Tensor(X_test)
testDataset = TensorDataset(tensor_y,tensor_x) # create your datset

ValueError: could not determine the shape of object type 'DataFrame'

In [54]:
from torch.utils.data import TensorDataset
from torch.utils.data import DataLoader

tensor_x = torch.Tensor(genre_labels.iloc[:len(newX)].values) # transform to torch tensor
tensor_y = torch.Tensor(newX)
my_dataset = TensorDataset(tensor_x,tensor_y) # create your datset

tensor([[0., 0., 1., 1., 0., 0., 0., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
         0., 0.],
        [0., 1., 0., 0., 0., 0., 0., 1., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
         0., 0.],
        [0., 0., 0., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0.,
         0., 0.],
        [0., 0., 0., 1., 0., 0., 1., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0.,
         0., 0.],
        [0., 0., 0., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
         0., 0.],
        [1., 0., 0., 0., 1., 0., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 1.,
         0., 0.],
        [0., 0., 0., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0.,
         0., 0.],
        [1., 1., 0., 0., 0., 0., 1., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
         0., 0.],
        [1., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 1.,
         0., 0.],
        [1., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 1.,
         0., 0.],
        [0

In [51]:
import torch
import torch.nn as nn
#from torchsummary import summary

class ResNet(nn.Module):
    def __init__(self, block, layers, num_classes=20):
        super(ResNet, self).__init__()
        self.block = block
        self.conv1 = nn.Conv2d(3, 64, kernel_size=7, stride=2, padding=3)
        self.bn1 = nn.BatchNorm2d(64)
        self.relu = nn.ReLU()
        self.maxpool = nn.MaxPool2d(kernel_size=3, stride=2, padding=1)

        #ResNet layers
        self.layer1 = self.new_layer(num_blocks=layers[0], in_channels=64, out_channels=64, stride=1)
        self.layer2 = self.new_layer(num_blocks=layers[1], in_channels=64, out_channels=128, stride=2)
        self.layer3 = self.new_layer(num_blocks=layers[2], in_channels=128, out_channels=256, stride=2)
        self.layer4 = self.new_layer(num_blocks=layers[3], in_channels=256, out_channels=512, stride=2)

        self.avgpool = nn.AdaptiveAvgPool2d((1, 1))
        self.fc = nn.Linear(512, num_classes)

    def forward(self, x):
        print(x)
        print(type(x))
        #print("input: ", x.shape)
        x = self.conv1(x)
        #print("conv1: ", x.shape)
        x = self.bn1(x)
        #print("bn1: ", x.shape)
        x = self.relu(x)
        #print("relu: ", x.shape)
        x = self.maxpool(x)
        #print("maxpool: ", x.shape)

        x = self.layer1(x)
        #print("layer 1: ", x.shape)
        x = self.layer2(x)
        #print("layer 2: ", x.shape)
        x = self.layer3(x)
        #print("layer 3: ", x.shape)
        x = self.layer4(x)
        #print("layer 4: ", x.shape)

        x = self.avgpool(x)
        x = x.reshape(x.shape[0], -1)
        x = self.fc(x)

        return x
    
    def new_layer(self, num_blocks, in_channels, out_channels, stride):
        layers = []
        layers.append(self.block(in_channels, out_channels))
        intermediate_channels = out_channels
        for i in range(num_blocks):
            layers.append(self.block(intermediate_channels, out_channels))
           
        return nn.Sequential(*layers)

class Block(nn.Module):
    def __init__(self, in_channels, out_channels, stride=1):
        super(Block, self).__init__()
        self.in_channels = in_channels
        self.out_channels = out_channels

        self.conv1 = nn.Conv2d(in_channels, out_channels, kernel_size=3, stride=stride, padding=1)
        self.bn1 = nn.BatchNorm2d(out_channels)
        self.conv2 = nn.Conv2d(out_channels, out_channels, kernel_size=3, stride=stride, padding=1)
        self.bn2 = nn.BatchNorm2d(out_channels)
        self.conv3 = nn.Conv2d(out_channels, out_channels, kernel_size=3, stride=stride, padding=1)
        self.bn3 = nn.BatchNorm2d(out_channels)
        self.conv4 = nn.Conv2d(out_channels, out_channels, kernel_size=3, stride=stride, padding=1)
        self.bn4 = nn.BatchNorm2d(out_channels)
        self.relu = nn.ReLU()

        self.identity = nn.Conv2d(in_channels, out_channels, kernel_size=1, stride=stride, padding=0)

    def forward(self, x):
        identity = x.clone()
        if self.in_channels != self.out_channels:
            identity = self.identity(identity)
        #print("id1", identity.shape)

        x = self.conv1(x)
        x = self.bn1(x)
        x = self.relu(x)
        x = self.conv2(x)
        x = self.bn2(x)
        x = self.relu(x)

        #Skip connection 1
        #print("id2", identity.shape, x.shape)
        x += identity
        identity = x.clone()
        #print("id3", identity.shape)

        x = self.conv3(x)
        x = self.bn3(x)
        x = self.relu(x)
        x = self.conv4(x)
        x = self.bn4(x)
        x = self.relu(x)

        #Skip connection 2
        x += identity

        x = self.relu(x)

        return x

def ResNet34():
    return ResNet(Block, [3, 4, 6, 3])

model = ResNet34()
#summary(model, input_size=(3, 224, 224), batch_size=1)

In [ ]:
import torch
import torch.nn as nn
from torch.autograd import Variable
from torchvision import transforms
from torch.utils.data.dataset import Dataset  # For custom datasets
#from data_pytorch import Data
#from rotnet import RotNet
import time
import shutil
import yaml

#parser = argparse.ArgumentParser(description='Configuration details for training/testing rotation net')
#parser.add_argument('--config', type=str, required=True)
#parser.add_argument('--train', action='store_true')
#parser.add_argument('--data_dir', type=str, required=True)
#parser.add_argument('--image', type=str)
#parser.add_argument('--model_number', type=str, required=True)

#args = parser.parse_args()

#config = yaml.load(open(args.config, 'r'), Loader=yaml.FullLoader)

"""
epochs = 10

for epoch in range(epochs):
    total_loss = 0
    
    #for batch in train_dataloader:
    for i, data in enumerate(train_dataloader, 0):
        #print(i)
        #print(data)
        #X_batch, y_batch = batch[0], batch[1] #.view(-1, 784)
        #print(y_batch)
        #print(X_batch, y_batch)
        #print(X_batch, y_batch)
        # THESE 5 LINES ARE IMPORTANT, UNDERSTAND WHAT IS HAPPENING HERE
        optimizer.zero_grad()
        predicted_batch = model(data) 
        #print(predicted_batch)
        loss = criterion(predicted_batch, y_batch)
        #print(loss)
        loss.backward()
        optimizer.step()
        total_loss += loss
        
        
       
    print("Epoch {0}: {1}".format(epoch, total_loss))
    #if epoch%5 == 0 and epoch != 0:
    #    test_batch = next(iter(test_dataloader))
    #    X_test, y_test = test_batch[0].view(-1, 784), test_batch[1]
    #    predicted = model(X_test)
    #    test_acc = torch.sum(y_test == torch.argmax(predicted, dim=1), dtype=torch.double) / len(y_test)
    #    print("\tTest Accuracy {0}".format(test_acc))
"""

def train(train_loader, model, criterion, optimizer, epoch):
    model.train()
    total_loss = 0
    for i, (test, train) in enumerate(train_loader):
        optimizer.zero_grad()
        predicted_batch = model(train)
        loss = criterion(predicted_batch, test)
        loss.backward()
        optimizer.step()
        total_loss += loss
        print(total_loss)
    """ 
    for i, (input, target) in enumerate(train_loader):
        optimizer.zero_grad()
        predicted_batch = model(input)
        loss = criterion(predicted_batch, y_batch)
        loss.backward()
        optimizer.step()
        total_loss += loss
    """

def validate(val_loader, model, criterion):
    model.eval()
    total_loss = 0
    for i, (input, target) in enumerate(val_loader):
        #optimizer.zero_grad()
        outputs = model(input)
        loss = criterion(target, outputs)
        total_loss += loss
        print(total_loss)
        #TODO: implement the validation. Remember this is validation and not training
        #so some things will be different.

def save_checkpoint(state, best_one, filename='rotationnetcheckpoint.pth.tar', filename2='rotationnetmodelbest.pth.tar'):
    torch.save(state, filename)
    #best_one stores whether your current checkpoint is better than the previous checkpoint
    if best_one:
        shutil.copyfile(filename, filename2)

def main():
    n_epochs = 10 #config["num_epochs"]
    model = ResNet34()
    criterion = torch.nn.MSELoss() #what is your loss function
    optimizer = torch.optim.SGD(model.parameters(), lr=0.0001, momentum = 0.9) #temp
    train_dataset = loadImages()
    train_dataloader = DataLoader(my_dataset, batch_size=256, shuffle=True)
    #val_loader = #how will you get your dataset
    #val_loader = #how will you use pytorch's function to build a dataloader
    for epoch in range(n_epochs):
            train(train_dataloader, model, criterion, optimizer, epoch)
            
         #TODO: make your loop which trains and validates. Use the train() func

         #TODO: Save your checkpoint

if __name__ == "__main__":
    main()

tensor([[[[0.0039, 0.5098, 0.7647,  ..., 0.7451, 0.0078, 0.4941],
          [0.7451, 0.0078, 0.4941,  ..., 0.5176, 0.7686, 0.0000],
          [0.5176, 0.7686, 0.0000,  ..., 0.0000, 0.5216, 0.7765],
          ...,
          [0.4627, 0.5451, 0.4000,  ..., 0.0039, 0.5333, 0.7843],
          [0.0000, 0.5922, 0.8392,  ..., 0.4980, 0.3608, 0.1412],
          [0.4980, 0.3490, 0.1412,  ..., 0.4275, 0.5294, 0.5569]],

         [[0.6235, 0.7412, 0.6157,  ..., 0.0000, 0.5373, 0.7922],
          [0.0000, 0.5922, 0.8392,  ..., 0.4980, 0.3608, 0.1412],
          [0.4980, 0.3608, 0.1373,  ..., 0.6431, 0.7176, 0.6706],
          ...,
          [0.2314, 0.7922, 0.4549,  ..., 0.5529, 0.7961, 0.0000],
          [0.5569, 0.8078, 0.0039,  ..., 0.0039, 0.6078, 0.8431],
          [0.6275, 0.6118, 0.6784,  ..., 0.1686, 0.6431, 0.4588]],

         [[0.1922, 0.6196, 0.4157,  ..., 0.5490, 0.7922, 0.0000],
          [0.5490, 0.8000, 0.0000,  ..., 0.0000, 0.6039, 0.8392],
          [0.6196, 0.6078, 0.6824,  ..., 0

tensor(5.1326, grad_fn=<AddBackward0>)
tensor([[[[0.0039, 0.5098, 0.7647,  ..., 0.7451, 0.0078, 0.4941],
          [0.7451, 0.0078, 0.4941,  ..., 0.5176, 0.7686, 0.0000],
          [0.5176, 0.7686, 0.0000,  ..., 0.0000, 0.5216, 0.7765],
          ...,
          [0.4627, 0.5451, 0.4000,  ..., 0.0039, 0.5333, 0.7843],
          [0.0000, 0.5922, 0.8392,  ..., 0.4980, 0.3608, 0.1412],
          [0.4980, 0.3490, 0.1412,  ..., 0.4275, 0.5294, 0.5569]],

         [[0.6235, 0.7412, 0.6157,  ..., 0.0000, 0.5373, 0.7922],
          [0.0000, 0.5922, 0.8392,  ..., 0.4980, 0.3608, 0.1412],
          [0.4980, 0.3608, 0.1373,  ..., 0.6431, 0.7176, 0.6706],
          ...,
          [0.2314, 0.7922, 0.4549,  ..., 0.5529, 0.7961, 0.0000],
          [0.5569, 0.8078, 0.0039,  ..., 0.0039, 0.6078, 0.8431],
          [0.6275, 0.6118, 0.6784,  ..., 0.1686, 0.6431, 0.4588]],

         [[0.1922, 0.6196, 0.4157,  ..., 0.5490, 0.7922, 0.0000],
          [0.5490, 0.8000, 0.0000,  ..., 0.0000, 0.6039, 0.8392],
   

In [25]:
for i in range(len(movies['popularity'])): 
    movies['popularity'][i] = movies['popularity'][i]/10

/Users/anshverma/opt/anaconda3/envs/python37/lib/python3.7/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


KeyError: 32

In [ ]:
movies['popularity']

In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F

class Net(nn.Module):

    def __init__(self):
        super(Net, self).__init__()
        # 1 input image channel, 6 output channels, 5x5 square convolution
        # kernel
        #self.conv1 = nn.Conv2d(1, 6, 5)
        #self.conv2 = nn.Conv2d(6, 16, 5)
        # an affine operation: y = Wx + b
        #self.fc1 = nn.Linear(16 * 5 * 5, 120)  # 5*5 from image dimension
        self.fc1 = nn.Linear(20, 15)
        self.fc2 = nn.Linear(15, 10)
        #self.fc2 = nn.Linear(16, )
        #self.fc3 = nn.Linear(84, 10)

    def forward(self, x):
        # Max pooling over a (2, 2) window
        #x = F.max_pool2d(F.relu(self.conv1(x)), (2, 2))
        # If the size is a square, you can specify with a single number
        #x = F.max_pool2d(F.relu(self.conv2(x)), 2)
        #x = x.view(-1, self.num_flat_features(x))
        #x = F.relu(self.fc1(x))
        #x = F.relu(self.fc2(x))
        #x = self.fc3(x)
        x = F.relu(self.fc1(x))
        x = F.relu(self.fc2(x))
        return x

    #def num_flat_features(self, x):
    #    size = x.size()[1:]  # all dimensions except the batch dimension
    #    num_features = 1
    #    for s in size:
    #        num_features *= s
    #    return num_features

net = Net()
print(net) 

In [ ]:
train_dataloader = DataLoader(my_dataset, batch_size=256, shuffle=True)
model1 = ResNet34()
nlpModel = tf.keras.models.load_model('savedNlpModel')
finalTrainingData = []
for i, (test, train) in enumerate(train_dataloader):
    genre1 = model1(train)
    genre2 = nlpModel(train)
    finalTrainingData.append(genre1 + genre2)

finalTrainingData = np.array(finalTrainingData)

In [ ]:
from torch.utils.data import TensorDataset
from torch.utils.data import DataLoader

tensor_x = torch.Tensor(finalTrainingData) # transform to torch tensor
tensor_y = torch.Tensor(movies['popularity'])
my_dataset = TensorDataset(tensor_x,tensor_y) # create your dataset

In [ ]:
def main():
    n_epochs = 10 #config["num_epochs"]
    model = Net() #
    criterion = torch.nn.MSELoss() #what is your loss function
    optimizer = torch.optim.SGD(model.parameters(), lr=0.001) #temp
    train_dataset = loadImages()
    train_dataloader = DataLoader(my_dataset, batch_size=256, shuffle=True)
    #val_loader = #how will you get your dataset
    #val_loader = #how will you use pytorch's function to build a dataloader
    for epoch in range(n_epochs):
            train(train_dataloader, model, criterion, optimizer, epoch)
     
         #TODO: make your loop which trains and validates. Use the train() func

         #TODO: Save your checkpoint

main()

In [ ]:
for value in range(len(epoch)):
    net(model)

In [ ]:
def resNetOutput():
    for image in images: 
        genre = model(image)